In [1]:
from rich.console import Console
from rich.traceback import install

# install(show_locals=True)
install()

console = Console()

In [2]:
from langchain.embeddings import SentenceTransformerEmbeddings
from langchain.text_splitter import RecursiveCharacterTextSplitter
import pandas as pd

from lib.dataframe_loader import DataFrameLoader
from lib.chroma import Chroma

In [3]:
FILE_DIR = "../../Dataset/Contracts_Dataset_With_Extract.csv"
# FILE_DIR = "../../Dataset/Tenders WA UTF8.csv"

In [4]:
# Load the data
df = pd.read_csv(FILE_DIR, index_col=False)

In [5]:
df = df.fillna("")

In [6]:
df.head()

Reference Number                     Client Agency        Type of Work  \
0          ARA201901891           Animal Resources Centre  Goods and Services   
1             20221AGWA  Art Gallery of Western Australia  Goods and Services   
2         FIN873DLGSCAG  Art Gallery of Western Australia  Goods and Services   
3            2020153WAM  Art Gallery of Western Australia  Goods and Services   
4  CUAHRS202117042023AC            Arts and Culture Trust  Goods and Services   

                                      Contract Title  \
0      Supply and Delivery of Aspen Bedding Material   
1  Bar Consultancy and Staffing AGWA Rooftop Bar ...   
2             Investment Services for Art Gallery WA   
3                     Provision of Audience Research   
4                Consultancy Services for HR Support   

                                         Description  Tender Closing Date  \
0  The Customer requires a Contractor to provide ...  2019-07-09 00:00:00   
1  The Art Gallery of Western Australia (AGWA) re...  2022-08-12 00:00:00   
2  Through this Request, the Art Gallery of Weste...  2021-05-04 00:00:00   
3  Provision of Audience Research. This research ...  2022-02-04 00:00:00   
4  Provision of specialist services to undertake ...  2023-06-02 00:00:00   

   UNSPSC Code                                       UNSPSC Title  \
0     41102614                   Research animal bedding material   
1     80101500  Business and corporate management consultation...   
2     84121706                 Financial asset management service   
3     80141500                                    Market research   
4     80110000                           Human resources services   

   Procurement Method  Revised Contract Value  \
0                Open                500000.0   
1  Open Advertisement               4303279.0   
2                Open                830300.0   
3  Open Advertisement                300795.0   
4                 CUA                 71000.0   

                      Supplier Name  \
0           Specialty Feeds Pty Ltd   
1  Ten Foot Tall Management Pty Ltd   
2                            JBWere   
3        Morris Hargreaves McIntyre   
4    Price Consulting Group Pty Ltd   

                                     Tenders Content  
0                                                     
1  Request Staffing AGWA PM Issued behalf Custome...  
2  INSERT NAME Table No Description DEFINITIONS D...  
3                                                     
4

In [53]:
console.log(type(df["UNSPSC Code"][0]))

[23:13:19] <class 'numpy.int64'>                                                                    ]8;id=425676;file:///var/folders/31/3s1dqvqd7wggr7v72rx0gfj00000gn/T/ipykernel_79287/1287719319.py\1287719319.py]8;;\:]8;id=794320;file:///var/folders/31/3s1dqvqd7wggr7v72rx0gfj00000gn/T/ipykernel_79287/1287719319.py#1\1]8;;\

In [8]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 26475 entries, 0 to 26474
Data columns (total 12 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   Reference Number        26475 non-null  object 
 1   Client Agency           26475 non-null  object 
 2   Type of Work            26475 non-null  object 
 3   Contract Title          26475 non-null  object 
 4   Description             26475 non-null  object 
 5   Tender Closing Date     26475 non-null  object 
 6   UNSPSC Code             26475 non-null  int64  
 7   UNSPSC Title            26475 non-null  object 
 8   Procurement Method      26475 non-null  object 
 9   Revised Contract Value  26475 non-null  float64
 10  Supplier Name           26475 non-null  object 
 11  Tenders Content         26475 non-null  object 
dtypes: float64(1), int64(1), object(10)
memory usage: 2.4+ MB


In [9]:
# date_format = "%Y-%m-%d %H:%M:%S"

df["Tender Closing Date Timestamp"] = pd.to_datetime(
    df["Tender Closing Date"], format="%Y-%m-%d %H:%M:%S"
)
# df["Tender Closing Date Timestamp"] = df["Tender Closing Date Timestamp"].apply(lambda x: int(x.timestamp()))
df["Tender Closing Date Timestamp"] = df["Tender Closing Date Timestamp"].apply(
    lambda x: int(x.strftime("%Y%m%d%H%M%S"))
)

In [10]:
console.log(df["Tender Closing Date"][0])
df.info()

[22:44:44] 2019-07-09 00:00:00                                                                      ]8;id=797305;file:///var/folders/31/3s1dqvqd7wggr7v72rx0gfj00000gn/T/ipykernel_79287/2701650213.py\2701650213.py]8;;\:]8;id=486201;file:///var/folders/31/3s1dqvqd7wggr7v72rx0gfj00000gn/T/ipykernel_79287/2701650213.py#1\1]8;;\

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 26475 entries, 0 to 26474
Data columns (total 13 columns):
 #   Column                         Non-Null Count  Dtype  
---  ------                         --------------  -----  
 0   Reference Number               26475 non-null  object 
 1   Client Agency                  26475 non-null  object 
 2   Type of Work                   26475 non-null  object 
 3   Contract Title                 26475 non-null  object 
 4   Description                    26475 non-null  object 
 5   Tender Closing Date            26475 non-null  object 
 6   UNSPSC Code                    26475 non-null  int64  
 7   UNSPSC Title                   26475 non-null  object 
 8   Procurement Method             26475 non-null  object 
 9   Revised Contract Value         26475 non-null  float64
 10  Supplier Name                  26475 non-null  object 
 11  Tenders Content                26475 non-null  object 
 12  Tender Closing Date Timestamp  26475 non-null 

In [11]:
loader = DataFrameLoader(df, page_content_columns=[])

data = loader.load()

In [12]:
from langchain.schema import Document


def chunk_docs(
    docs: list[Document], max_chunk_size: int, overlap: int = -1
) -> list[Document]:
    """
    Chunk documents into smaller documents
    :param docs: Documents
    :param metadatas: Documents metadata
    :param max_chunk_size:
    :param overlap: - if -1 then overlap is 10% of max_chunk_size
    :return:
    """
    _overlap = overlap
    if _overlap == -1:
        _overlap = int(max_chunk_size * 0.1)
    text_splitter = RecursiveCharacterTextSplitter(
        chunk_size=max_chunk_size, chunk_overlap=_overlap, add_start_index=True
    )
    _out_docs = text_splitter.split_documents(docs)
    return _out_docs


docs = chunk_docs(data, 512)

In [13]:
# embeddings = SentenceTransformerEmbeddings(model_name="thenlper/gte-base", model_kwargs = {'device': 'mps'})
embeddings = SentenceTransformerEmbeddings(
    model_name="all-MiniLM-L6-v2", model_kwargs={"device": "mps"}
)

In [14]:
# def split_list(input_list, chunk_size):
#     for i in range(0, len(input_list), chunk_size):
#         yield input_list[i : i + chunk_size]


# split_docs_chunked = split_list(docs, 41000)

# for split_docs_chunk in split_docs_chunked:
#     vectordb = Chroma.from_documents(
#         documents=split_docs_chunk,
#         embedding=embeddings,
#         persist_directory="./chroma_db",
#         collection_metadata={"hnsw:space": "cosine"},
#     )
#     vectordb.persist()

In [15]:
db_disk = Chroma(
    persist_directory="./chroma_db",
    embedding_function=embeddings,
    collection_metadata={"hnsw:space": "cosine"},
)

In [63]:
from dataclasses import dataclass
from datetime import datetime
from chromadb.api.types import Where


def format_date(date_string: str, date_format: str = "%Y-%m-%d") -> int:
    # date_format = "%Y-%m-%d %H:%M:%S"
    # Convert string to datetime object
    date_object = datetime.strptime(date_string, date_format)
    # Convert datetime object to "YYYYMMDDHHMMSS" format
    return int(date_object.strftime("%Y%m%d%H%M%S"))


@dataclass
class Query:
    query: str
    startDate: str | None = None
    endDate: str | None = None
    Range: list[int] | None = None
    typeOfWork: str | None = None
    UNSPSCcode: list[int] | None = None

    def get_filters(self) -> Where | None:
        filters = {"$and": []}
        if self.startDate:
            filters["$and"].append(
                {"Tender Closing Date Timestamp": {"$gte": format_date(self.startDate)}}
            )
        if self.endDate:
            filters["$and"].append(
                {"Tender Closing Date Timestamp": {"$lte": format_date(self.endDate)}}
            )
        if self.Range:
            filters["$and"].append(
                {
                    "Revised Contract Value": {
                        "$gte": self.Range[0],
                    }
                }
            )
            filters["$and"].append(
                {
                    "Revised Contract Value": {
                        "$lte": self.Range[1],
                    }
                }
            )
        if self.typeOfWork:
            filters["$and"].append({"Type of Work": self.typeOfWork})
        if self.UNSPSCcode:
            filters["$and"].append({"UNSPSC Code": {"$in": self.UNSPSCcode}})
        if len(filters["$and"]) == 1:
            filters = filters["$and"][0]
        elif len(filters["$and"]) == 0:
            filters = None
        return filters

In [81]:
query_dict = {
    "query": "CCTV Contracts",
    # "startDate": "2023-03-10",
    # "endDate": "2023-04-20",
    # "Range": [90000, 100000],
    "typeOfWork": "Works",
    # "UNSPSCcode": [80172000, 41102614, 80110000],
}


query = Query(**query_dict)

console.log(query.get_filters())

[23:32:36] {'Type of Work': 'Works'}                                                               ]8;id=232587;file:///var/folders/31/3s1dqvqd7wggr7v72rx0gfj00000gn/T/ipykernel_79287/3698930904.py\3698930904.py]8;;\:]8;id=543354;file:///var/folders/31/3s1dqvqd7wggr7v72rx0gfj00000gn/T/ipykernel_79287/3698930904.py#13\13]8;;\

In [21]:
query_embedding = embeddings.embed_query(query.query)
matching_docs = db_disk.similarity_search_by_vector_with_relevance_scores(
    query_embedding, k=245000
)

console.log(len(matching_docs))

[22:46:36] 245000                                                                                   ]8;id=786571;file:///var/folders/31/3s1dqvqd7wggr7v72rx0gfj00000gn/T/ipykernel_79287/3473641418.py\3473641418.py]8;;\:]8;id=7128;file:///var/folders/31/3s1dqvqd7wggr7v72rx0gfj00000gn/T/ipykernel_79287/3473641418.py#6\6]8;;\

In [57]:
console.log(type(matching_docs[0][0].metadata["UNSPSC Code"]))

[23:16:18] <class 'int'>                                                                            ]8;id=491347;file:///var/folders/31/3s1dqvqd7wggr7v72rx0gfj00000gn/T/ipykernel_79287/3987989664.py\3987989664.py]8;;\:]8;id=289949;file:///var/folders/31/3s1dqvqd7wggr7v72rx0gfj00000gn/T/ipykernel_79287/3987989664.py#1\1]8;;\

In [82]:
num_filtered_docs = len(db_disk.get(where=query.get_filters())["documents"])

k_filtered = int(num_filtered_docs * 0.95)
console.log(k_filtered)

[23:33:08] 178901                                                                                   ]8;id=437028;file:///var/folders/31/3s1dqvqd7wggr7v72rx0gfj00000gn/T/ipykernel_79287/2335218336.py\2335218336.py]8;;\:]8;id=371979;file:///var/folders/31/3s1dqvqd7wggr7v72rx0gfj00000gn/T/ipykernel_79287/2335218336.py#4\4]8;;\

In [83]:
matching_docs_filtered = db_disk.similarity_search_by_vector_with_relevance_scores(
    query_embedding, k=k_filtered, filter=query.get_filters()
)

# console.log(len(matching_docs_filtered))

In [84]:
# just get the Tender Closing Date from the metadata
dates_filtered = [
    doc.metadata["Revised Contract Value"]
    for doc, similarity_score in matching_docs_filtered
]

console.log(len(dates_filtered))

[23:35:06] 178901                                                                                   ]8;id=727909;file:///var/folders/31/3s1dqvqd7wggr7v72rx0gfj00000gn/T/ipykernel_79287/2373605411.py\2373605411.py]8;;\:]8;id=97834;file:///var/folders/31/3s1dqvqd7wggr7v72rx0gfj00000gn/T/ipykernel_79287/2373605411.py#7\7]8;;\

In [18]:
result_dict = {}
for doc, score in matching_docs:
    row_id = doc.metadata["row"]
    if row_id not in result_dict:
        result_dict[row_id] = score
    else:
        result_dict[row_id] = min(result_dict[row_id], score)

In [19]:
import numpy as np
import plotly.express as px

# Convert keys and values to numpy arrays
keys = np.array(list(map(str, result_dict.keys())))
values = 1 - np.array(list(result_dict.values()))
total = np.array(list(range(1, len(keys) + 1)))

# Create a DataFrame
df = pd.DataFrame({"Row ID": keys, "Similarity Score": values, "Total": total})

# Create the plot
fig = px.line(df, x="Row ID", y="Similarity Score", custom_data=["Total"])

fig.update_traces(
    hovertemplate="<br>".join(
        [
            "Row ID: %{x}",
            "Similarity Score: %{y}",
            "Total: %{customdata[0]}",
        ]
    )
)

# Display the plot
fig.show()

In [20]:
result_dict = {}
for doc, score in matching_docs:
    row_id = doc.metadata["row"]
    if row_id not in result_dict:
        doc.metadata["similarity_score"] = score
        result_dict[row_id] = doc.metadata
        result_dict[row_id]["sentence_piece"] = doc.page_content
        result_dict[row_id].pop("row")
        result_dict[row_id].pop("start_index")
    else:
        if result_dict[row_id]["similarity_score"] > score:
            result_dict[row_id]["similarity_score"] = score
            result_dict[row_id]["sentence_piece"] = doc.page_content

values_list = list(result_dict.values())